# Test Cycle detection

This notebook tests the cycle detection and extraction code.

In [1]:
import os
import pandas as pd
import utilities.preprocess_raw_data as prep_data
import utilities.plotting as plots

In [2]:
MERGED_PATH = "./data/my_datasets/merged.parquet"
if os.path.exists(MERGED_PATH):
    df = pd.read_parquet(MERGED_PATH)
else:
    df = prep_data.load_and_merge_raw_dfs()
    df.to_parquet(MERGED_PATH)

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 281111 entries, 0 to 288939
Data columns (total 7 columns):
 #   Column                 Non-Null Count   Dtype              
---  ------                 --------------   -----              
 0   device_uuid            281111 non-null  object             
 1   battery_level_percent  281111 non-null  float64            
 2   radio_level_percent    281111 non-null  int64              
 3   fw_version             281111 non-null  object             
 4   status_time            281111 non-null  datetime64[ns, UTC]
 5   air_temperature        281111 non-null  float64            
 6   battery_type_id        281111 non-null  float64            
dtypes: datetime64[ns, UTC](1), float64(3), int64(1), object(2)
memory usage: 17.2+ MB


In [4]:
df = prep_data.drop_insufficient_data(df, column="device_uuid")

Dropped 74251 entries from 6 device_uuid because they were insufficient.


In [5]:
df = prep_data.calculate_daily_mean(df)

In [6]:
df = prep_data.smooth_df_using_median(df)

In [7]:
df = prep_data.drop_insufficient_data(df, column="device_uuid")

Dropped 1833 entries from 7 device_uuid because they were insufficient.


In [8]:
df = prep_data.label_df_peaks(df)

In [9]:
plots.plot_devices_and_peaks(df)

In [10]:
df = prep_data.extract_cycles(df)

In [11]:
plots.plot_cycles(df)

In [12]:
df = prep_data.drop_insufficient_data(df, column="cycle_id", count_thresh=30)

Dropped 6390 entries from 89 cycle_id because they were insufficient.


In [13]:
fw_versions = df.groupby(by="cycle_id")["fw_version"].unique()
pd.merge(df, fw_versions, on="cycle_id", how="left")

device_uuid status_time  \
0      00082fe6-1ce0-43a0-ae8b-f42a36f5b2cc  2022-07-21   
1      00082fe6-1ce0-43a0-ae8b-f42a36f5b2cc  2022-07-22   
2      00082fe6-1ce0-43a0-ae8b-f42a36f5b2cc  2022-07-23   
3      00082fe6-1ce0-43a0-ae8b-f42a36f5b2cc  2022-07-24   
4      00082fe6-1ce0-43a0-ae8b-f42a36f5b2cc  2022-07-25   
...                                     ...         ...   
25330  fa0a7c25-fe90-41ea-a368-a1186038efb4  2023-06-07   
25331  fa0a7c25-fe90-41ea-a368-a1186038efb4  2023-06-08   
25332  fa0a7c25-fe90-41ea-a368-a1186038efb4  2023-06-09   
25333  fa0a7c25-fe90-41ea-a368-a1186038efb4  2023-06-10   
25334  fa0a7c25-fe90-41ea-a368-a1186038efb4  2023-06-13   

       battery_level_percent  radio_level_percent  air_temperature  \
0                     91.000               100.00         3.510671   
1                     91.000                91.25         3.517777   
2                     91.000               100.00         3.194710   
3                     91.000                97.50         2.856155   
4                     91.000               100.00         2.453636   
...                      ...                  ...              ...   
25330                 98.750               100.00         8.671024   
25331                 99.000               100.00         7.412807   
25332                 98.875               100.00         3.601410   
25333                 99.000               100.00         3.500736   
25334                 99.000               100.00         5.928085   

       battery_type_id fw_version_x  battery_diff  peak_label  \
0                  1.0       v01.49         0.000       False   
1                  1.0       v01.49         0.000       False   
2                  1.0       v01.49         0.000       False   
3                  1.0       v01.49         0.000       False   
4                  1.0       v01.49         0.000       False   
...                ...          ...           ...         ...   
25330              1.0       v01.49        -0.125       False   
25331              1.0       v01.49         0.250       False   
25332              1.0       v01.49        -0.125       False   
25333              1.0       v01.49         0.125       False   
25334              1.0       v01.49         0.125       False   

       left_peak_border  right_peak_border  cycle_id fw_version_y  
0                 False              False         0     [v01.49]  
1                 False              False         0     [v01.49]  
2                 False              False         0     [v01.49]  
3                 False              False         0     [v01.49]  
4                 False              False         0     [v01.49]  
...                 ...                ...       ...          ...  
25330             False              False       284     [v01.49]  
25331             False              False       284     [v01.49]  
25332             False              False       284     [v01.49]  
25333             False              False       284     [v01.49]  
25334             False              False       284     [v01.49]  

[25335 rows x 13 columns]

In [14]:
plots.plot_cycles(df)

In [15]:
plots.plot_devices_and_peaks(df)

In [16]:
plots.plot_cycles(df, grouped_by_device=True)